# Webscraping & Applied ML

## Description : 

La description du projet se trouve dans le word 

## Scrapping

Our sources are Google Flight and ICAO.

Google flights : https://www.google.com/travel/flights?hl=fr

ICAO : https://www.icao.int/environmental-protection/Carbonoffset/Pages/default.aspx

The objective is to scrap some data that we can use for our case.

Imports :

In [1]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import TimeoutException
from bs4 import BeautifulSoup
import pandas as pd
import time
import logging
from datetime import datetime
from selenium import webdriver
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.common.by import By
from selenium.webdriver.common.keys import Keys
from bs4 import BeautifulSoup
import time

In [2]:
# Initialize the WebDriver
service = Service(r'C:\Users\deslo\.wdm\drivers\chromedriver\win64\131.0.6778.108\chromedriver-win32\chromedriver.exe')
driver = webdriver.Chrome(service=service)

# Open Google Flights
driver.get('https://www.google.com/travel/flights?hl=en')

In [3]:
#part to scrap data from google flights :
def input_search_criteria(origin, destination, travel_departure):

    date_input = WebDriverWait(driver, 10).until(
        EC.presence_of_element_located((By.CSS_SELECTOR, '[aria-label="Departure"]'))
    )
    date_input.clear()
    date_input.send_keys(travel_departure)
    time.sleep(1)
    date_input.send_keys(Keys.ENTER)


    origin_input = WebDriverWait(driver, 10).until(
        EC.presence_of_element_located((By.CSS_SELECTOR, '[aria-label="Where from?"]'))
    )
    origin_input.clear()
    origin_input.send_keys(origin)
    origin_input.send_keys(Keys.ENTER)

    time.sleep(1)
    destination_input = WebDriverWait(driver, 10).until(
        EC.presence_of_element_located((By.CSS_SELECTOR, '[aria-label="Where to?"]'))
    )
    destination_input.clear()
    destination_input.send_keys(destination)
    time.sleep(1)
    #click on the first suggestion
    click_first_suggestion = WebDriverWait(driver, 10).until(
        EC.presence_of_element_located((By.CSS_SELECTOR, '[class="zsRT0d"]'))
    )
    click_first_suggestion.click()
    time.sleep(3)

    all_flights_button = WebDriverWait(driver, 20).until(
        EC.element_to_be_clickable((By.CSS_SELECTOR, '[aria-label="View flights"]'))
    )
    driver.execute_script("arguments[0].target='_self';", all_flights_button)
    all_flights_button.click()

    # Attendre que la page des vols se charge
    WebDriverWait(driver, 20).until(
        lambda d: "/flights" in d.current_url
    )
    print(f"URL actuelle : {driver.current_url}")

    # Charger le contenu de la page avec BeautifulSoup
    soup = BeautifulSoup(driver.page_source, 'html.parser')

    filter_button = WebDriverWait(driver, 10).until(
        EC.element_to_be_clickable((By.CSS_SELECTOR, '[aria-label="All filters"]'))
    )
    filter_button.click()

    WebDriverWait(driver, 10).until(
        EC.presence_of_element_located((By.CSS_SELECTOR, 'div[jslog^="138066"]'))
    )


    


def scrape_flight_data():
    flight_data = []
    time.sleep(10)
    soup = BeautifulSoup(driver.page_source, 'html.parser')

    # Trouvez toutes les divs contenant les vols
    flight_divs = soup.select('div', {'jsname': '1iWDBC'})
    if not flight_divs:
        print("La div contenant les vols n'a pas été trouvée.")
        return []
# Verify the current URL
    current_url = driver.current_url
    print(f"Current URL1: {current_url}")


    # Trouvez tous les <li> dans ces divs
    flight_listings = []
    for div in flight_divs:
        flight_listings.extend(div.find_all('li'))

    print(f"Nombre de vols trouvés : {len(flight_listings)}")

    for flight in flight_listings:
        try:
            # Heure de départ
            departure_time_span = flight.find('span', {'aria-label': lambda x: x and 'Departure time' in x})
            departure_time = departure_time_span.get_text(strip=True) if departure_time_span else None

            arrival_time_span = flight.find('span', {'aria-label': lambda x: x and 'Arrival time' in x})
            arrival_time = arrival_time_span.get_text(strip=True) if arrival_time_span else None

            airline = flight.find('div', {'class': 'sSHqwe tPgKwe ogfYpf'}).get_text(strip=True) if flight.find('div', {'class': 'sSHqwe tPgKwe ogfYpf'}) else 'N/A'

            price_span = flight.find('span', {'aria-label': lambda x: x and 'euros' in x})
            price = price_span.get_text(strip=True) if price_span else 'N/A'

            emissions = flight.find('div', {'class': 'N6PNV ogfYpf juCwOd BYjnCf'}).get_text(strip=True) if flight.find('div', {'class': 'N6PNV ogfYpf juCwOd BYjnCf'}) else 'N/A'


            # Ajouter les données collectées dans un dictionnaire
            flight_data.append({
                'Departure Time': departure_time,
                'Arrival Time': arrival_time,
                'Airline': airline,
                'Price': price,
                'Emission': emissions,
              
            })

        except Exception as e:
            print(f"Erreur lors de l'extraction d'un vol : {e}")

    return flight_data

input_search_criteria('Paris', 'Barcelona', '10/02/2025')

# Scrape flight data

flight_data = scrape_flight_data()
print(flight_data)
# Convert to DataFrame
# Verify the current URL
current_url = driver.current_url
print(f"Current URL3: {current_url}")
df = pd.DataFrame(flight_data)
df.head()
print(df)
df.info()


URL actuelle : https://www.google.com/travel/flights?tfs=CBsQAhooEgoyMDI1LTEwLTAyagwIAhIIL20vMDVxdGpyDAgCEggvbS8wMWY2MhooEgoyMDI1LTEwLTA2agwIAhIIL20vMDFmNjJyDAgCEggvbS8wNXF0akABSAFSA0VVUnABemxDalJJVkVSNGRVRnRMWHBXVkZsQlJVWkRUMEZDUnkwdExTMHRMUzB0TFMxM1ptcG9ORUZCUVVGQlIyUXdTemRaU1RoT2NFdEJFZ1pHVWpNeE1qSWFDZ2lTUEJBQ0dnTkZWVkk0SEhDaVBnPT2YAQGyARIYASABKgwIAxIIL20vMDFmNjI&tfu=GgA&hl=en&sa=X&ved=0CAoQtY0DahgKEwiYrZb-xdKKAxUAAAAAHQAAAAAQjQE
Current URL1: https://www.google.com/travel/flights/search?tfs=CBwQAhooEgoyMDI1LTEwLTAyagwIAhIIL20vMDVxdGpyDAgCEggvbS8wMWY2MhooEgoyMDI1LTEwLTA2agwIAhIIL20vMDFmNjJyDAgCEggvbS8wNXF0akABSAFwAYIBCwj___________8BmAEB&tfu=CmxDalJJVkVSNGRVRnRMWHBXVkZsQlJVWkRUMEZDUnkwdExTMHRMUzB0TFMxM1ptcG9ORUZCUVVGQlIyUXdTemRaU1RoT2NFdEJFZ1pHVWpNeE1qSWFDZ2lTUEJBQ0dnTkZWVkk0SEhDaVBnPT0&hl=en&sa=X&ved=0CAoQtY0DahgKEwiYrZb-xdKKAxUAAAAAHQAAAAAQjQE
Nombre de vols trouvés : 4725
[{'Departure Time': None, 'Arrival Time': None, 'Airline': 'N/A', 'Price': 'N/A', 'Emission': 'N/A'}, {'Depar

In [4]:
#combien de nan dans le dataframe
print(df.isnull().sum())
#montrer les non null
print(df.notnull().sum())



Departure Time    4221
Arrival Time      4221
Airline              0
Price                0
Emission             0
dtype: int64
Departure Time     504
Arrival Time       504
Airline           4725
Price             4725
Emission          4725
dtype: int64


In [5]:

print("source :",driver.page_source)

source : <html lang="en" dir="ltr"><head><style nonce="">.LGLeeN-keyboard-shortcuts-view{display:-webkit-box;display:-webkit-flex;display:-moz-box;display:-ms-flexbox;display:flex}.LGLeeN-keyboard-shortcuts-view table,.LGLeeN-keyboard-shortcuts-view tbody,.LGLeeN-keyboard-shortcuts-view td,.LGLeeN-keyboard-shortcuts-view tr{background:inherit;border:none;margin:0;padding:0}.LGLeeN-keyboard-shortcuts-view table{display:table}.LGLeeN-keyboard-shortcuts-view tr{display:table-row}.LGLeeN-keyboard-shortcuts-view td{-moz-box-sizing:border-box;box-sizing:border-box;display:table-cell;color:#000;padding:6px;vertical-align:middle;white-space:nowrap}.LGLeeN-keyboard-shortcuts-view td:first-child{text-align:end}.LGLeeN-keyboard-shortcuts-view td kbd{background-color:#e8eaed;border-radius:2px;border:none;-moz-box-sizing:border-box;box-sizing:border-box;color:inherit;display:inline-block;font-family:Google Sans Text,Roboto,Arial,sans-serif;line-height:16px;margin:0 2px;min-height:20px;min-width:20p

 all_filters_button = WebDriverWait(driver, 10).until(
        EC.presence_of_element_located((By.CLASS_NAME, 'VfPpkd-LgbsSe VfPpkd-LgbsSe-OWXEXe-Bz112c-M1Soyc VfPpkd-LgbsSe-OWXEXe-dgl2Hf ksBjEc lKxP2d LQeN7 bRx3h x4Vnpe yJQRU sIWnMc hNyRxf cd29Sd'))
    )
    all_filters_button.click()

    less_emissions = WebDriverWait(driver, 10).until(
    EC.presence_of_element_located((By.CSS_SELECTOR, '[aria-label="Less emissions only"]'))
    )
    less_emissions.click()